<h1 align=center><font size = 5>Segmenting and Clustering Neighborhoods in Finland</font></h1>

## Introduction

In this note book is investigated the similarity between neighborhoods in the tenth biggest cities in Finland. Cities and their neighborhoods are retrieved from open data sources and neighborhood addresses are converted into their equivalent latitude and longitude values. Foursquare API is used to to explore neighborhoods to get the most common venue categories in each neighborhood, and then the neighborhoods are grouped into clusters. The *k*-means clustering algorithm is used to complete this task. Finally, the Folium library is used to visualize the neighborhoods in Finland and their emerging clusters.

## Table of Contents

<div class="alert alert-block alert-info" style="margin-top: 20px">

<font size = 3>

1. <a href="#item1">Download and Explore Dataset</a>

2. <a href="#item2">Explore Neighborhoods in Finland</a>

3. <a href="#item3">Analyze Each Neighborhood</a>

4. <a href="#item4">Cluster Neighborhoods</a>

5. <a href="#item5">Examine Clusters</a>    
</font>
</div>

Before we get the data and start exploring it, let's download all the dependencies that we will need.

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/DSX-Python35

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    certifi-2018.8.24          |        py35_1001         139 KB  conda-forge
    ca-certificates-2019.3.9   |       hecc5488_0         146 KB  conda-forge
    geopy-1.19.0               |             py_0          53 KB  conda-forge
    openssl-1.0.2r             |       h14c3975_0         3.1 MB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         3.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.49-py_0         conda-forge
    geopy:           1.19.0-py_0       conda-forge

The following packages will be UPDATED:

   

<a id='item1'></a>

## 1. Download and Explore Dataset

We need to know, which are ten biggest cities in Finland and their neighborhoods. 

Luckily this information exists for free on the web and actually there a lot more informations available, if needed in future.

Let's download the data.

In [2]:
!wget -q -O 'Finland_cities.xlsx' https://www.kuntaliitto.fi/sites/default/files/media/file/Kuntajaot%20ja%20asukasluvut%202000-2018_2.xls

In [3]:
!wget -q -O 'Neighborhoods_by_postal_code.xlsx' https://www.stat.fi/static/media/uploads/tup/paavo/alueryhmittely_posnro_2015.xlsx
print('Data downloaded!')

Data downloaded!


#### Load and explore the data

Next, let's load the data and formulate it as needed.

First cities ...

In [4]:
cities_df = pd.read_excel('Finland_cities.xlsx',header=9,sheet_name="2018")
cities_df = cities_df.drop(index=[0,1,2], columns=['Kuntanro','Unnamed: 3'])
cities_df = cities_df.sort_values(by=['Asukasluku'],ascending=False)
cities_df = cities_df.rename(columns={'Kunta':'City','Asukasluku':'Inhabitants'})
cities_df = cities_df.head(10)
cities_df

City Inhabitants
36    Helsinki      643272
14       Espoo      279044
271    Tampere      231853
294     Vantaa      223027
183       Oulu      201810
279      Turku      189669
66   Jyväskylä      140188
126     Lahti       119573
117     Kuopio      118209
204       Pori       84587

Then neighborhoods

In [5]:
neighborhoods_df = pd.read_excel('Neighborhoods_by_postal_code.xlsx',header=4, converters={'Postinumeroalue': np.str})
# Let's drop columns, which are not needed
neighborhoods_df = neighborhoods_df.drop(['Postinumeroalueen nimi (sv)','Kunnan nimi (sv)','Kunta','Kuntaryhmä','Kuntaryhmän nimi','Seutukunta','Seutukunnan nimi','Maakunta','Maakunnan nimi','Suuralue','Suuralueen nimi','AVI','AVI:n nimi','ELY','ELY:n nimi','NUTS 1','NUTS 1 nimi','NUTS 2','NUTS 2 nimi','NUTS 3','NUTS 3 nimi','Sairaanhoitopiiri','Sairaanhoitopiirin nimi','Vaalipiiri','Vaalipiirin nimi','Hovioikeus','Hovioikeuden nimi','Käräjäoikeus','Käräjäoikeuden nimi'],axis=1)
neighborhoods_df = neighborhoods_df.rename(columns={'Kunnan nimi':'City','Postinumeroalueen nimi':'Neighborhood', 'Postinumeroalue':'Postal_code'})
neighborhoods_df.head(10)

Postal_code     Neighborhood      City
0       62710         Kurejoki  Alajärvi
1       62720          Sissala  Alajärvi
2       62730         Haukkala  Alajärvi
3       62740      Koskenvarsi  Alajärvi
4       62750       Saukonkylä  Alajärvi
5       62760       Menkijärvi  Alajärvi
6       62830        Luoma-Aho  Alajärvi
7       62900  Alajärvi Keskus  Alajärvi
8       62920         Levijoki  Alajärvi
9       62940           Hoisko  Alajärvi

Merge cities and neighborhoods into one dataframe...

In [6]:
dtype = {'City': str}
neighborhoods_df = pd.merge(cities_df.astype(dtype), neighborhoods_df.astype(dtype), on='City', how='right')
neighborhoods_df = neighborhoods_df.dropna()

Let's take a quick look at the data.

In [7]:
neighborhoods_df.head()

City Inhabitants Postal_code       Neighborhood
0  Helsinki      643272       00100  Helsinki Keskusta
1  Helsinki      643272       00120          Punavuori
2  Helsinki      643272       00130    Kaartinkaupunki
3  Helsinki      643272       00140        Kaivopuisto
4  Helsinki      643272       00150               Eira

Then let's loop through the dataframe and fill the dataframe one row at a time with location information.

#### Use geopy library to get the latitude and longitude values of neighborhoods.

In [8]:
geolocator = Nominatim(user_agent="city_explorer")
latitudes = []
longitudes = []

# THIS IS VERY SLOW AND SOMETIMES UNREALIABLE

for row in neighborhoods_df.itertuples(index=False):   
    address = row.Neighborhood + ' ' + row.Neighborhood
    location = geolocator.geocode(address)
    if location is not None:
        latitude = float(location.latitude)
        longitude = float(location.longitude)
        latitudes.append(latitude)
        longitudes.append(longitude)
    else:
# In case that geolocator cannot return coordinates,, let's just use dummy coordinateds
        latitudes.append('60.1713')
        longitudes.append('24.9415')
#    print('The geograpical coordinate of neighborhood are {}, {}.'.format(latitude, longitude))
   
# Create a column from the list
neighborhoods_df['Latitude'] = latitudes
neighborhoods_df['Longitude'] = longitudes


Quickly examine the resulting dataframe.

In [9]:
neighborhoods_df.head()

City Inhabitants Postal_code       Neighborhood Latitude Longitude
0  Helsinki      643272       00100  Helsinki Keskusta  60.1713   24.9415
1  Helsinki      643272       00120          Punavuori  60.1638    24.941
2  Helsinki      643272       00130    Kaartinkaupunki  60.1652   24.9472
3  Helsinki      643272       00140        Kaivopuisto  60.1565   24.9552
4  Helsinki      643272       00150               Eira  60.1554   24.9423

Let's check the number of cities and neighborhoods.

In [10]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods_df['City'].unique()) + 1,
        neighborhoods_df.shape[0]
    )
)

The dataframe has 10 boroughs and 402 neighborhoods.


#### Create a map of Finland with neighborhoods superimposed on top.

In [11]:
# create map of Finland using latitude and longitude values
map_Finland = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods_df['Latitude'], neighborhoods_df['Longitude'], neighborhoods_df['City'], neighborhoods_df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [float(lat), float(lng)],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Finland)  
    
map_Finland

**Folium** is a great visualization library. Feel free to zoom into the above map, and click on each circle mark to reveal the name of the neighborhood and its respective borough.

However, for illustration purposes, let's simplify the above map and segment and cluster only the neighborhoods in Tampere. So let's slice the original dataframe and create a new dataframe of the Tampere data.

In [12]:
Tampere_data = neighborhoods_df[neighborhoods_df['City'] == 'Tampere'].reset_index(drop=True)
Tampere_data.head()

City Inhabitants Postal_code             Neighborhood Latitude Longitude
0  Tampere      231853       33100           Tampere Keskus  61.4981   23.7625
1  Tampere      231853       33180        Lapinniemi-Käpylä  60.1713   24.9415
2  Tampere      231853       33200  Tampere Keskus Läntinen  60.1713   24.9415
3  Tampere      231853       33210    Itä-Amuri-Tammerkoski  60.1713   24.9415
4  Tampere      231853       33230              Länsi-Amuri  61.5016   23.7455

Let's get the geographical coordinates of Tampere.

In [13]:
address = 'Tampere, Finland'

geolocator = Nominatim(user_agent="Tampere_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Tampere are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Tampere are 61.4980214, 23.7603118.


As we did with whole Finland, let's visualize Tampere and the neighborhoods in it.

In [14]:
# create map of Tampere using latitude and longitude values
map_Tampere = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(Tampere_data['Latitude'], Tampere_data['Longitude'], Tampere_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [float(lat), float(lng)],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_Tampere)  
    
map_Tampere

Next, let's start utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [15]:
CLIENT_ID = '0HQIHYZISENIUFGGB2DHSZ13M15IQ5ALXDWWB1LOOOIJZDKI' # your Foursquare ID
CLIENT_SECRET = 'SOHGVYX2N5H5M111L3NDCW450FML0SU5XTML5OGLK2AJ1HSC' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 0HQIHYZISENIUFGGB2DHSZ13M15IQ5ALXDWWB1LOOOIJZDKI
CLIENT_SECRET:SOHGVYX2N5H5M111L3NDCW450FML0SU5XTML5OGLK2AJ1HSC


#### Let's explore the first neighborhood in our dataframe.

Get the neighborhood's name.

In [16]:
Tampere_data.loc[0, 'Neighborhood']

'Tampere Keskus'

Get the neighborhood's latitude and longitude values.

In [17]:
neighborhood_latitude = Tampere_data.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = Tampere_data.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = Tampere_data.loc[0, 'Neighborhood'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of Tampere Keskus are 61.49813535, 23.7624813688609.


#### Now, let's get the top 100 venues that are in Tampere Keskus within a radius of 500 meters.

First, let's create the GET request URL. Name your URL **url**.

In [18]:
LIMIT = 100 
radius = 500 
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
    CLIENT_ID, 
    CLIENT_SECRET, 
    VERSION, 
    neighborhood_latitude, 
    neighborhood_longitude, 
    radius, 
    LIMIT)
url # display URL




'https://api.foursquare.com/v2/venues/explore?&client_id=0HQIHYZISENIUFGGB2DHSZ13M15IQ5ALXDWWB1LOOOIJZDKI&client_secret=SOHGVYX2N5H5M111L3NDCW450FML0SU5XTML5OGLK2AJ1HSC&v=20180605&ll=61.49813535,23.7624813688609&radius=500&limit=100'

Send the GET request and examine the resutls

In [19]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5ccbe65a4434b9316a53cd92'},
 'response': {'groups': [{'items': [{'reasons': {'count': 0,
       'items': [{'reasonName': 'globalInteractionReason',
         'summary': 'This spot is popular',
         'type': 'general'}]},
      'referralId': 'e-0-508e8372e4b09ddc8004fbab-0',
      'venue': {'categories': [{'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/steakhouse_',
          'suffix': '.png'},
         'id': '4bf58dd8d48988d1cc941735',
         'name': 'Steakhouse',
         'pluralName': 'Steakhouses',
         'primary': True,
         'shortName': 'Steakhouse'}],
       'id': '508e8372e4b09ddc8004fbab',
       'location': {'address': 'Aleksis Kiven katu 13',
        'cc': 'FI',
        'city': 'Tampere',
        'country': 'Suomi',
        'distance': 218,
        'formattedAddress': ['Aleksis Kiven katu 13',
         '33200 Tampere',
         'Suomi'],
        'labeledLatLngs': [{'label': 'display',
          'lat': 61.4964558

All the information is in the *items* key. Before we proceed, let's create the **get_category_type** function.

In [20]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Let's clean the json and structure it into a *pandas* dataframe.

In [21]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name      categories        lat        lng
0         Ravinteli Huber      Steakhouse  61.496456  23.760365
1   Tampereen Kauppahalli  Farmers Market  61.496802  23.758918
2                 Kaffila            Café  61.496663  23.760322
3  Pyynikin munkkikahvila            Café  61.497593  23.761052
4   Fazer Café Hämeenkatu            Café  61.497795  23.762822

Let's check how many venues were returned by Foursquare?

In [22]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

68 venues were returned by Foursquare.


<a id='item2'></a>

## 2. Explore Neighborhoods in Finland

#### Let's create a function to repeat the same process to all the neighborhoods in Finland

In [23]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *Finland_venues*.

In [24]:
LIMIT = 100 
radius = 500

Finland_venues = getNearbyVenues(names=neighborhoods_df['Neighborhood'],
                                   latitudes=neighborhoods_df['Latitude'],
                                   longitudes=neighborhoods_df['Longitude']
                                  )



#### Let's check the size of the resulting dataframe

In [25]:
print(Finland_venues.shape)
Finland_venues.head()

(11993, 7)


Neighborhood Neighborhood Latitude Neighborhood Longitude  \
0  Helsinki Keskusta               60.1713                24.9415   
1  Helsinki Keskusta               60.1713                24.9415   
2  Helsinki Keskusta               60.1713                24.9415   
3  Helsinki Keskusta               60.1713                24.9415   
4  Helsinki Keskusta               60.1713                24.9415   

                      Venue  Venue Latitude  Venue Longitude  \
0          Habitat Helsinki       60.169557        24.942441   
1                   Ateneum       60.170302        24.943788   
2  Suomen Kansallisteatteri       60.172510        24.943740   
3           Pien Shop & Bar       60.169673        24.944526   
4                 FreshStop       60.172603        24.940047   

           Venue Category  
0  Furniture / Home Store  
1              Art Museum  
2                 Theater  
3              Beer Store  
4             Coffee Shop

Let's check how many venues were returned for each neighborhood

In [26]:
Finland_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                                   
Ahkionlahti-Vianta                               100                     100   
Aitolahti                                          1                       1   
Ammattikorkeakoulu                                 8                       8   
Askisto                                            4                       4   
Atala-Linnainmaa                                 100                     100   
Aurinkolahti                                       6                       6   
Eira                                              52                      52   
Epilä                                              8                       8   
Espoon Keskus Itäinen                            100                     100   
Espoon Keskus Läntinen                           100                     100   
Espoonlahti                                       31                      31   
Etelä-Haaga                                       11                      11   
Etelä-Laajasalo                                    9                       9   
Etelä-Leppävaara                                  39                      39   
Etelä-Vuosaari                                    28                      28   
Etu-Niirala                                      100                     100   
Etu-Vallila                                       37                      37   
Friisilä                                           9                       9   
Haapalehto                                         4                       4   
Hakunila                                          10                      10   
Halssila                                           4                       4   
Haukilahti                                        10                      10   
Haukiluoma-Ikuri                                 100                     100   
Haukipudas Asemanseutu                           100                     100   
Haukipudas Keskus                                100                     100   
Heinäpää                                          13                      13   
Helsinki Keskusta                                100                     100   
Herttoniemi                                       37                      37   
Hervanta                                          36                      36   
Hiekkaharju                                        7                       7   
Hirvilahti-Salonkulma                            100                     100   
Hiukkavaara                                        2                       2   
Huhkola-Lauste-Vaala                             100                     100   
Huhtasuo                                           6                       6   
Hämevaara                                          4                       4   
Härmälä-Rantaperkiö                              100                     100   
Höyhtyä                                            7                       7   
Iinatti                                            1                       1   
Iivisniemi                                        10                      10   
Ilmala                                            11                      11   
Ilpoinen-Harittu                                 100                     100   
Impola                                             4                       4   
Iso-Heikkilä                                       5                       5   
Isojoenranta                                       2                       2   
Itä-Amuri-Tammerkoski                            100                     100   
Itä-Hakkila                                        3                       3   
Itä-Karttula-Riuttasenpää                        100                     100   
Itä-Pakila                                         8                       8   
Itä-Pasila                     

#### Let's find out how many unique categories can be curated from all the returned venues

In [27]:
print('There are {} uniques categories.'.format(len(Finland_venues['Venue Category'].unique())))

There are 336 uniques categories.


<a id='item3'></a>

## 3. Analyze Each Neighborhood

In [28]:
# one hot encoding
Finland_onehot = pd.get_dummies(Finland_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Finland_onehot['Neighborhood'] = Finland_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Finland_onehot.columns[-1]] + list(Finland_onehot.columns[:-1])
Finland_onehot = Finland_onehot[fixed_columns]

Finland_onehot.head()

Zoo  ATM  Accessories Store  African Restaurant  American Restaurant  \
0    0    0                  0                   0                    0   
1    0    0                  0                   0                    0   
2    0    0                  0                   0                    0   
3    0    0                  0                   0                    0   
4    0    0                  0                   0                    0   

   Amphitheater  Antique Shop  Aquarium  Argentinian Restaurant  Art Gallery  \
0             0             0         0                       0            0   
1             0             0         0                       0            0   
2             0             0         0                       0            0   
3             0             0         0                       0            0   
4             0             0         0                       0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           1                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Auditorium  Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  \
0           0            0              0                0          0   
1           0            0              0                0          0   
2           0            0              0                0          0   
3           0            0              0                0          0   
4           0            0              0                0          0   

   Baby Store  Badminton Court  Bagel Shop  Bakery  Bar  Baseball Field  \
0           0                0           0       0    0               0   
1           0                0           0       0    0               0   
2           0                0           0       0    0               0   
3           0                0           0       0    0               0   
4           0                0           0       0    0               0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Bay  Beach  \
0                 0                 0                   0    0      0   
1                 0                 0                   0    0      0   
2                 0                 0                   0    0      0   
3                 0                 0                   0    0      0   
4                 0                 0                   0    0      0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Bike Trail  Bistro  \
0                0         0            0           0           0       0   
1                0         0            0           0           0       0   
2                0         0            0           0           0       0   
3                0         0            0           1           0       0   
4                0         0            0           0           0       0   

   Board Shop  Boat or Ferry  Bookstore  Border Crossing  Boutique  \
0           0              0          0                0         0   
1           0              0          0                0         0   
2           0              0          0                0         0   
3           0              0          0                0         0   
4           0              0          0                0         0   

   Bowling Alley  Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0           0                     0               0        0   
1              0           0                     0               0        0   
2              0           0                     0               0        0   
3              0           0                     0               0        0   
4     

And let's examine the new dataframe size.

In [29]:
Finland_onehot.shape

(11993, 336)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [30]:
Finland_grouped = Finland_onehot.groupby('Neighborhood').mean().reset_index()
Finland_grouped

Neighborhood       Zoo       ATM  Accessories Store  \
0               Ahkionlahti-Vianta  0.000000  0.000000               0.01   
1                        Aitolahti  0.000000  0.000000               0.00   
2               Ammattikorkeakoulu  0.000000  0.000000               0.00   
3                          Askisto  0.000000  0.000000               0.00   
4                 Atala-Linnainmaa  0.000000  0.000000               0.01   
5                     Aurinkolahti  0.000000  0.000000               0.00   
6                             Eira  0.000000  0.000000               0.00   
7                            Epilä  0.000000  0.000000               0.00   
8            Espoon Keskus Itäinen  0.000000  0.000000               0.01   
9           Espoon Keskus Läntinen  0.000000  0.000000               0.01   
10                     Espoonlahti  0.000000  0.000000               0.00   
11                     Etelä-Haaga  0.000000  0.000000               0.00   
12                 Etelä-Laajasalo  0.000000  0.000000               0.00   
13                Etelä-Leppävaara  0.000000  0.000000               0.00   
14                  Etelä-Vuosaari  0.000000  0.000000               0.00   
15                     Etu-Niirala  0.000000  0.000000               0.01   
16                     Etu-Vallila  0.027027  0.000000               0.00   
17                        Friisilä  0.000000  0.000000               0.00   
18                      Haapalehto  0.000000  0.000000               0.00   
19                        Hakunila  0.000000  0.000000               0.00   
20                        Halssila  0.000000  0.000000               0.00   
21                      Haukilahti  0.000000  0.000000               0.00   
22                Haukiluoma-Ikuri  0.000000  0.000000               0.01   
23          Haukipudas Asemanseutu  0.000000  0.000000               0.01   
24               Haukipudas Keskus  0.000000  0.000000               0.01   
25                        Heinäpää  0.000000  0.000000               0.00   
26               Helsinki Keskusta  0.000000  0.000000               0.01   
27                     Herttoniemi  0.000000  0.000000               0.00   
28                        Hervanta  0.000000  0.027778               0.00   
29                     Hiekkaharju  0.000000  0.000000               0.00   
30           Hirvilahti-Salonkulma  0.000000  0.000000               0.01   
31                     Hiukkavaara  0.000000  0.000000               0.00   
32            Huhkola-Lauste-Vaala  0.000000  0.000000               0.01   
33                        Huhtasuo  0.000000  0.000000               0.00   
34                       Hämevaara  0.000000  0.000000               0.00   
35             Härmälä-Rantaperkiö  0.000000  0.000000               0.01   
36                         Höyhtyä  0.000000  0.000000               0.00   
37                         Iinatti  0.000000  0.000000               0.00   
38                      Iivisniemi  0.000000  0.000000               0.00   
39                          Ilmala  0.000000  0.000000               0.00   
40                Ilpoinen-Harittu  0.000000  0.000000               0.01   
41                          Impola  0.000000  0.000000               0.00   
42                    Iso-Heikkilä  0.000000  0.000000               0.00   
43                    Isojoenranta  0.000000  0.000000               0.00   
44           Itä-Amuri-Tammerkoski  0.000000  0.000000               0.01   
45                     Itä-Hakkila  0.000000  0.000000               0.00   
46       Itä-Karttula-Riuttasenpää  0.000000  0.000000               0.01   
47                      Itä-Pakila  0.000000  0.000000               0.00   
48                      Itä-Pasila  0.000000  0.000000               0.00   
49            Itäkeskus-Marjaniemi  0.000000  0.000000               0.01   
50                       Jakkukylä  0.000000  0.000000               0.00   
51                

#### Let's confirm the new size

In [31]:
Finland_grouped.shape

(341, 336)

#### Let's print each neighborhood along with the top 5 most common venues

In [32]:
num_top_venues = 5

for hood in Finland_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = Finland_grouped[Finland_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Ahkionlahti-Vianta----
            venue  freq
0            Café  0.08
1     Coffee Shop  0.05
2  Clothing Store  0.04
3    Burger Joint  0.03
4      Art Museum  0.03


----Aitolahti----
                           venue  freq
0                          Diner   1.0
1                            Zoo   0.0
2                   Optical Shop   0.0
3  Paper / Office Supplies Store   0.0
4           Pakistani Restaurant   0.0


----Ammattikorkeakoulu----
                  venue  freq
0           Flea Market  0.12
1          Optical Shop  0.12
2    Basketball Stadium  0.12
3        Clothing Store  0.12
4  Gym / Fitness Center  0.12


----Askisto----
           venue  freq
0         Bakery  0.25
1            Bar  0.25
2  Grocery Store  0.25
3        Dog Run  0.25
4      Nightclub  0.00


----Atala-Linnainmaa----
            venue  freq
0            Café  0.08
1     Coffee Shop  0.05
2  Clothing Store  0.04
3    Burger Joint  0.03
4      Art Museum  0.03


----Aurinkolahti----
                

#### Let's put that into a *pandas* dataframe

First, let's write a function to sort the venues in descending order.

In [33]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [34]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = Finland_grouped['Neighborhood']

for ind in np.arange(Finland_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Finland_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Ahkionlahti-Vianta                  Café           Coffee Shop   
1           Aitolahti                 Diner           Yoga Studio   
2  Ammattikorkeakoulu        Clothing Store                  Park   
3             Askisto                Bakery                   Bar   
4    Atala-Linnainmaa                  Café           Coffee Shop   

  3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
0        Clothing Store  Furniture / Home Store            Art Museum   
1           Fish Market                    Fair    Falafel Restaurant   
2           Flea Market      Basketball Stadium          Soccer Field   
3         Grocery Store                 Dog Run                  Fair   
4        Clothing Store  Furniture / Home Store            Art Museum   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0          Burger Joint             Juice Bar                Bakery   
1                  Farm        Farmers Market  Fast Food Restaurant   
2           Men's Store  Gym / Fitness Center          Optical Shop   
3    Falafel Restaurant                  Farm        Farmers Market   
4          Burger Joint             Juice Bar                Bakery   

  9th Most Common Venue 10th Most Common Venue  
0              Boutique                Brewery  
1                 Field    Filipino Restaurant  
2           Yoga Studio                   Fair  
3  Fast Food Restaurant                  Field  
4              Boutique                Brewery

<a id='item4'></a>

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 5 clusters.

In [35]:
# set number of clusters
kclusters = 5

Finland_grouped_clustering = Finland_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(Finland_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 0, 4, 0, 0, 0, 0, 0, 0], dtype=int32)

In [36]:
Finland_grouped_clustering.head()

Zoo  ATM  Accessories Store  African Restaurant  American Restaurant  \
0  0.0  0.0               0.01                 0.0                  0.0   
1  0.0  0.0               0.00                 0.0                  0.0   
2  0.0  0.0               0.00                 0.0                  0.0   
3  0.0  0.0               0.00                 0.0                  0.0   
4  0.0  0.0               0.01                 0.0                  0.0   

   Amphitheater  Antique Shop  Aquarium  Argentinian Restaurant  Art Gallery  \
0           0.0           0.0       0.0                     0.0         0.01   
1           0.0           0.0       0.0                     0.0         0.00   
2           0.0           0.0       0.0                     0.0         0.00   
3           0.0           0.0       0.0                     0.0         0.00   
4           0.0           0.0       0.0                     0.0         0.01   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0        0.03                 0.01               0.0                 0.0   
1        0.00                 0.00               0.0                 0.0   
2        0.00                 0.00               0.0                 0.0   
3        0.00                 0.00               0.0                 0.0   
4        0.03                 0.01               0.0                 0.0   

   Auditorium  Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  \
0         0.0          0.0            0.0              0.0        0.0   
1         0.0          0.0            0.0              0.0        0.0   
2         0.0          0.0            0.0              0.0        0.0   
3         0.0          0.0            0.0              0.0        0.0   
4         0.0          0.0            0.0              0.0        0.0   

   Baby Store  Badminton Court  Bagel Shop  Bakery   Bar  Baseball Field  \
0         0.0              0.0         0.0    0.03  0.01             0.0   
1         0.0              0.0         0.0    0.00  0.00             0.0   
2         0.0              0.0         0.0    0.00  0.00             0.0   
3         0.0              0.0         0.0    0.25  0.25             0.0   
4         0.0              0.0         0.0    0.03  0.01             0.0   

   Baseball Stadium  Basketball Court  Basketball Stadium  Bay  Beach  \
0               0.0               0.0               0.000  0.0    0.0   
1               0.0               0.0               0.000  0.0    0.0   
2               0.0               0.0               0.125  0.0    0.0   
3               0.0               0.0               0.000  0.0    0.0   
4               0.0               0.0               0.000  0.0    0.0   

   Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  Bike Trail  Bistro  \
0              0.0      0.01          0.0        0.01         0.0     0.0   
1              0.0      0.00          0.0        0.00         0.0     0.0   
2              0.0      0.00          0.0        0.00         0.0     0.0   
3              0.0      0.00          0.0        0.00         0.0     0.0   
4              0.0      0.01          0.0        0.01         0.0     0.0   

   Board Shop  Boat or Ferry  Bookstore  Border Crossing  Boutique  \
0         0.0            0.0       0.01              0.0      0.02   
1         0.0            0.0       0.00              0.0      0.00   
2         0.0            0.0       0.00              0.0      0.00   
3         0.0            0.0       0.00              0.0      0.00   
4         0.0            0.0       0.01              0.0      0.02   

   Bowling Alley  Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  \
0            0.0         0.0                   0.0             0.0     0.02   
1            0.0         0.0                   0.0             0.0     0.00   
2            0.0         0.0                   0.0             0.0     0.00   
3            0.0         0.0                   0.0             0.0     0.00   


Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [37]:
neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Ahkionlahti-Vianta                  Café           Coffee Shop   
1           Aitolahti                 Diner           Yoga Studio   
2  Ammattikorkeakoulu        Clothing Store                  Park   
3             Askisto                Bakery                   Bar   
4    Atala-Linnainmaa                  Café           Coffee Shop   

  3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
0        Clothing Store  Furniture / Home Store            Art Museum   
1           Fish Market                    Fair    Falafel Restaurant   
2           Flea Market      Basketball Stadium          Soccer Field   
3         Grocery Store                 Dog Run                  Fair   
4        Clothing Store  Furniture / Home Store            Art Museum   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0          Burger Joint             Juice Bar                Bakery   
1                  Farm        Farmers Market  Fast Food Restaurant   
2           Men's Store  Gym / Fitness Center          Optical Shop   
3    Falafel Restaurant                  Farm        Farmers Market   
4          Burger Joint             Juice Bar                Bakery   

  9th Most Common Venue 10th Most Common Venue  
0              Boutique                Brewery  
1                 Field    Filipino Restaurant  
2           Yoga Studio                   Fair  
3  Fast Food Restaurant                  Field  
4              Boutique                Brewery

In [38]:
neighborhoods_df.head()

City Inhabitants Postal_code       Neighborhood Latitude Longitude
0  Helsinki      643272       00100  Helsinki Keskusta  60.1713   24.9415
1  Helsinki      643272       00120          Punavuori  60.1638    24.941
2  Helsinki      643272       00130    Kaartinkaupunki  60.1652   24.9472
3  Helsinki      643272       00140        Kaivopuisto  60.1565   24.9552
4  Helsinki      643272       00150               Eira  60.1554   24.9423

In [39]:
#Adding cluster labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
#Finland_merged = neighborhoods_df
#dtype = {'Neighborhood': str}
Finland_merged = pd.merge(neighborhoods_df, neighborhoods_venues_sorted, on='Neighborhood', how='left')


#Finland_merged = Finland_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood', how='left')
Finland_merged.head()

City Inhabitants Postal_code       Neighborhood Latitude Longitude  \
0  Helsinki      643272       00100  Helsinki Keskusta  60.1713   24.9415   
1  Helsinki      643272       00120          Punavuori  60.1638    24.941   
2  Helsinki      643272       00130    Kaartinkaupunki  60.1652   24.9472   
3  Helsinki      643272       00140        Kaivopuisto  60.1565   24.9552   
4  Helsinki      643272       00150               Eira  60.1554   24.9423   

   Cluster Labels    1st Most Common Venue 2nd Most Common Venue  \
0             0.0                     Café           Coffee Shop   
1             0.0  Scandinavian Restaurant              Beer Bar   
2             0.0  Scandinavian Restaurant                  Café   
3             0.0                     Park         Grocery Store   
4             0.0                     Park           Pizza Place   

  3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
0        Clothing Store          Burger Joint  Furniture / Home Store   
1           Coffee Shop                   Bar                    Park   
2                 Hotel                  Park  Furniture / Home Store   
3           Coffee Shop        Ice Cream Shop     Monument / Landmark   
4         Grocery Store        Ice Cream Shop           Boat or Ferry   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Bakery            Art Museum             Juice Bar   
1                 Wine Bar                  Café          Dance Studio   
2               Restaurant          Cocktail Bar        Clothing Store   
3               Playground            Restaurant       Border Crossing   
4  Scandinavian Restaurant            Playground     French Restaurant   

      9th Most Common Venue 10th Most Common Venue  
0                   Brewery   Gym / Fitness Center  
1  Mediterranean Restaurant             Restaurant  
2               Coffee Shop           Dance Studio  
3                 Nightclub                   Café  
4                    Bistro        Harbor / Marina

In [40]:
# Let's drop NaN rows and change coordinates to floats
Finland_merged = Finland_merged.dropna()
Finland_merged['Latitude'] = Finland_merged['Latitude'].astype(float)
Finland_merged['Longitude'] = Finland_merged['Longitude'].astype(float)

In [41]:
Finland_merged.dtypes
Finland_merged.head()

City Inhabitants Postal_code       Neighborhood   Latitude  Longitude  \
0  Helsinki      643272       00100  Helsinki Keskusta  60.171320  24.941457   
1  Helsinki      643272       00120          Punavuori  60.163824  24.940954   
2  Helsinki      643272       00130    Kaartinkaupunki  60.165214  24.947222   
3  Helsinki      643272       00140        Kaivopuisto  60.156452  24.955245   
4  Helsinki      643272       00150               Eira  60.155422  24.942340   

   Cluster Labels    1st Most Common Venue 2nd Most Common Venue  \
0             0.0                     Café           Coffee Shop   
1             0.0  Scandinavian Restaurant              Beer Bar   
2             0.0  Scandinavian Restaurant                  Café   
3             0.0                     Park         Grocery Store   
4             0.0                     Park           Pizza Place   

  3rd Most Common Venue 4th Most Common Venue   5th Most Common Venue  \
0        Clothing Store          Burger Joint  Furniture / Home Store   
1           Coffee Shop                   Bar                    Park   
2                 Hotel                  Park  Furniture / Home Store   
3           Coffee Shop        Ice Cream Shop     Monument / Landmark   
4         Grocery Store        Ice Cream Shop           Boat or Ferry   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Bakery            Art Museum             Juice Bar   
1                 Wine Bar                  Café          Dance Studio   
2               Restaurant          Cocktail Bar        Clothing Store   
3               Playground            Restaurant       Border Crossing   
4  Scandinavian Restaurant            Playground     French Restaurant   

      9th Most Common Venue 10th Most Common Venue  
0                   Brewery   Gym / Fitness Center  
1  Mediterranean Restaurant             Restaurant  
2               Coffee Shop           Dance Studio  
3                 Nightclub                   Café  
4                    Bistro        Harbor / Marina

Finally, let's visualize the resulting clusters

In [42]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Finland_merged['Latitude'], Finland_merged['Longitude'], Finland_merged['Neighborhood'], Finland_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
#        [60.1713, 24.9423],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)

       
map_clusters

<a id='item5'></a>

## 5. Examine Clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.

#### Cluster 1

In [43]:
Finland_merged.loc[Finland_merged['Cluster Labels'] == 0, Finland_merged.columns[[1] + list(range(5, Finland_merged.shape[1]))]]

Inhabitants  Longitude  Cluster Labels         1st Most Common Venue  \
0        643272  24.941457             0.0                          Café   
1        643272  24.940954             0.0       Scandinavian Restaurant   
2        643272  24.947222             0.0       Scandinavian Restaurant   
3        643272  24.955245             0.0                          Park   
4        643272  24.942340             0.0                          Park   
5        643272  24.980322             0.0                          Park   
6        643272  24.954733             0.0                   Pizza Place   
7        643272  24.909155             0.0                     Cafeteria   
8        643272  24.984239             0.0                          Café   
9        643272  24.878706             0.0                      Bus Stop   
10       643272  24.885968             0.0          Gym / Fitness Center   
11       643272  24.911655             0.0               Harbor / Marina   
12       643272  24.921239             0.0          Gym / Fitness Center   
13       643272  24.922298             0.0          Gym / Fitness Center   
14       643272  24.916733             0.0                          Park   
15       643272  24.941500             0.0                          Café   
16       643272  24.941500             0.0                          Café   
17       643272  24.900488             0.0             Indian Restaurant   
18       643272  24.908067             0.0                          Park   
19       643272  24.895447             0.0                          Park   
22       643272  24.874358             0.0                          Café   
23       643272  24.941500             0.0                          Café   
25       643272  24.856057             0.0                      Bus Stop   
26       643272  24.857849             0.0                      Bus Stop   
28       643272  24.846382             0.0            Chinese Restaurant   
30       643272  24.861226             0.0                         Plaza   
34       643272  24.964409             0.0               Thai Restaurant   
35       643272  24.953198             0.0                           Bar   
36       643272  24.939032             0.0                          Café   
37       643272  24.952451             0.0                           Bar   
38       643272  24.976684             0.0          Gym / Fitness Center   
39       643272  24.956710             0.0                  Tram Station   
40       643272  24.941500             0.0                          Café   
43       643272  25.018440             0.0                 Historic Site   
45       643272  24.946613             0.0                      Bus Stop   
47       643272  24.941500             0.0                          Café   
49       643272  24.975117             0.0                      Platform   
51       643272  24.931666             0.0                    Playground   
54       643272  25.010760             0.0          Gym / Fitness Center   
56       643272  24.994598             0.0                 Grocery Store   
57       643272  25.028561             0.0                   Pizza Place   
61       643272  25.079451             0.0                   Supermarket   
63       643272  25.011976             0.0                     Wine Shop   
64       643272  25.040027             0.0             Recreation Center   
65       643272  25.030177             0.0                      Bus Stop   
66       643272  25.059762             0.0                          Park   
67       643272  25.060476             0.0                Baseball Field   
70       643272  25.039690             0.0                        Museum   
72       643272  25.056318             0.0        Furniture / Home Store   
74       643272  25.086146             0.0                 Grocery Store   
75       643272  25.103034             0.0                          Park   
77       643272  24.941500             0.0          

#### Cluster 2

In [44]:
Finland_merged.loc[Finland_merged['Cluster Labels'] == 1, Finland_merged.columns[[1] + list(range(5, Finland_merged.shape[1]))]]

Inhabitants  Longitude  Cluster Labels 1st Most Common Venue  \
21       643272  24.891092             1.0              Bus Stop   
24       643272  24.879995             1.0              Bus Stop   
27       643272  24.872467             1.0              Bus Stop   
29       643272  24.883545             1.0              Bus Stop   
32       643272  24.900798             1.0              Bus Stop   
33       643272  24.880256             1.0              Bus Stop   
44       643272  24.964341             1.0              Bus Stop   
46       643272  24.939375             1.0              Bus Stop   
48       643272  24.956599             1.0              Bus Stop   
50       643272  24.929921             1.0              Bus Stop   
52       643272  24.960199             1.0              Bus Stop   
53       643272  24.952110             1.0              Bus Stop   
55       643272  25.010960             1.0              Bus Stop   
62       643272  24.993986             1.0     Convenience Store   
68       643272  25.044920             1.0              Bus Stop   
71       643272  25.051805             1.0              Bus Stop   
76       643272  25.063126             1.0              Bus Stop   
79       643272  25.107151             1.0              Bus Stop   
97       279044  24.693750             1.0              Bus Stop   
98       279044  24.712095             1.0              Bus Stop   
99       279044  24.703648             1.0              Bus Stop   
101      279044  24.667915             1.0              Bus Stop   
103      279044  24.651552             1.0              Bus Stop   
108      279044  24.782406             1.0              Bus Stop   
109      279044  24.764505             1.0              Bus Stop   
112      279044  24.807106             1.0              Bus Stop   
114      279044  24.735424             1.0              Bus Stop   
115      279044  24.740593             1.0              Bus Stop   
126      279044  24.710913             1.0              Bus Stop   
128      279044  24.654167             1.0              Bus Stop   
139      231853  23.569452             1.0              Bus Stop   
142      231853  23.706702             1.0                   Pub   
148      231853  23.859019             1.0              Bus Stop   
152      231853  23.844155             1.0           Golf Course   
165      223027  25.105685             1.0              Bus Stop   
167      223027  25.117747             1.0              Bus Stop   
188      223027  24.806439             1.0              Bus Stop   
193      223027  24.909235             1.0              Bus Stop   
200      223027  24.865175             1.0              Bus Stop   
201      223027  24.837955             1.0              Bus Stop   
223      201810  25.446506             1.0         Shopping Mall   
257      189669  22.305460             1.0              Bus Stop   
258      189669  22.367093             1.0                 Hotel   
340      118209  25.070724             1.0              Bus Stop   

       2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
21        Chinese Restaurant     Indian Restaurant          Intersection   
24              Optical Shop             Mini Golf            Taxi Stand   
27                 Cafeteria       Warehouse Store                Office   
29         Convenience Store         Train Station           Karaoke Bar   
32              Soccer Field         Grocery Store           Fish Market   
33         Convenience Store         Train Station           Karaoke Bar   
44               Pizza Place            Taxi Stand         Grocery Store   
46                 Cafeteria     Martial Arts Dojo     Indian Restaurant   
48             Grocery Store     Convenience Store        Knitting Store   
50         Convenience Store           Flower Shop              Pharmacy   
52               Pizza Place         Grocery Store         Historic Site   
53                    Bistro   

#### Cluster 3

In [45]:
Finland_merged.loc[Finland_merged['Cluster Labels'] == 2, Finland_merged.columns[[1] + list(range(5, Finland_merged.shape[1]))]]

Inhabitants  Longitude  Cluster Labels       1st Most Common Venue  \
211      201810  25.671038             2.0  Construction & Landscaping   
372       84587  21.780307             2.0  Construction & Landscaping   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
211           Yoga Studio           Fish Market                  Fair   
372           Yoga Studio           Fish Market                  Fair   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
211    Falafel Restaurant                  Farm        Farmers Market   
372    Falafel Restaurant                  Farm        Farmers Market   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
211  Fast Food Restaurant                 Field    Filipino Restaurant  
372  Fast Food Restaurant                 Field    Filipino Restaurant

#### Cluster 4

In [46]:
Finland_merged.loc[Finland_merged['Cluster Labels'] == 3, Finland_merged.columns[[1] + list(range(5, Finland_merged.shape[1]))]]

Inhabitants  Longitude  Cluster Labels 1st Most Common Venue  \
272      189669  22.227176             3.0                  Lake   
297      140188  25.682294             3.0                  Lake   
344      118209  24.168606             3.0                  Lake   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
272           Yoga Studio           Film Studio                  Fair   
297           Yoga Studio           Film Studio                  Fair   
344           Yoga Studio           Film Studio                  Fair   

    5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
272    Falafel Restaurant                  Farm        Farmers Market   
297    Falafel Restaurant                  Farm        Farmers Market   
344    Falafel Restaurant                  Farm        Farmers Market   

    8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
272  Fast Food Restaurant                 Field    Filipino Restaurant  
297  Fast Food Restaurant                 Field    Filipino Restaurant  
344  Fast Food Restaurant                 Field    Filipino Restaurant

#### Cluster 5

In [47]:
Finland_merged.loc[Finland_merged['Cluster Labels'] == 4, Finland_merged.columns[[1] + list(range(5, Finland_merged.shape[1]))]]

Inhabitants  Longitude  Cluster Labels   1st Most Common Venue  \
31       643272  24.876611             4.0           Grocery Store   
41       643272  25.008187             4.0                     Gym   
58       643272  24.990974             4.0                Bus Stop   
59       643272  25.048302             4.0           Grocery Store   
69       643272  25.079140             4.0           Historic Site   
104      279044  24.656273             4.0                Bus Stop   
134      231853  23.709773             4.0                     Pub   
158      231853  23.759478             4.0                     ATM   
160      231853  23.808307             4.0           Shopping Mall   
163      231853  23.900102             4.0              Playground   
168      223027  25.105249             4.0           Grocery Store   
170      223027  25.037313             4.0           Train Station   
171      223027  25.042492             4.0             Karaoke Bar   
179      223027  25.096952             4.0              Playground   
180      223027  25.137684             4.0              Playground   
189      223027  24.822726             4.0              Playground   
191      223027  24.871627             4.0           Grocery Store   
192      223027  24.782478             4.0                  Bakery   
194      223027  24.845668             4.0                     Bar   
197      223027  24.857157             4.0             Pizza Place   
203      201810  25.455517             4.0           Grocery Store   
205      201810  25.488654             4.0  Furniture / Home Store   
209      201810  25.577616             4.0             Pizza Place   
225      201810  25.419646             4.0             Pizza Place   
228      201810  25.575237             4.0              Playground   
229      201810  25.560946             4.0             Pizza Place   
232      201810  25.408441             4.0             Supermarket   
251      189669  22.157040             4.0                     Bar   
275      140188  25.756697             4.0           Grocery Store   
277      140188  25.760261             4.0           Grocery Store   
280      140188  25.801369             4.0       Convenience Store   
281      140188  25.795801             4.0            Soccer Field   
282      140188  25.838455             4.0         Motorcycle Shop   
285      140188  25.712225             4.0           Grocery Store   
288      140188  25.698038             4.0             Pizza Place   
290      140188  25.738266             4.0       Convenience Store   
291      140188  25.728774             4.0             Pizza Place   
293      140188  25.708509             4.0             Pizza Place   
296      140188  25.768151             4.0           Historic Site   
299      140188  25.645892             4.0            Skating Rink   
308      140188  25.455168             4.0                     Pub   
312      118209  27.613641             4.0                  Forest   
313      118209  27.651829             4.0           Grocery Store   
316      118209  27.636333             4.0                     Pub   
321      118209  27.654035             4.0           Grocery Store   
323      118209  27.705877             4.0           Grocery Store   
335      118209  28.163486             4.0           Grocery Store   
354      118209  27.300151             4.0           Grocery Store   
384       84587  24.773034             4.0                   River   
399       84587  22.583091             4.0           Grocery Store   

    2nd Most Common Venue       3rd Most Common Venue  \
31               Bus Stop                         Gym   
41     Chinese Restaurant               Grocery Store   
58          Grocery Store               Shopping Mall   
59                    Gym                         Pub   
69               Bus Stop                  Playground   
104           Pizza Place               Grocery Store   
134         Grocery Store         


This notebook was created by [Hannu Niittymaa](https://www.linkedin.com/in/hannu-niittymaa-055076a)  I hope you found this lab interesting and educational. Feel free to contact me if you have any questions!